**Практическая работа №4**


# Обнаружение злоумышленников в системе мобильных денежных переводов

_Вариант 5_


1) настройка окружения

In [4]:
# %pip install scipy==1.8.1
# %pip install networkx==2.7.0
# %pip install pyvis pandas numpy plotly

from functools import reduce
from pyvis import network as net

import pandas as pd
import numpy as np
import networkx as nx
import plotly.express as px
import plotly.graph_objects as go

from plotly.offline import iplot
from IPython.display import display, HTML




#for Jupiter notebooks
import plotly.io as pio #comment for Google collab
pio.renderers.default='notebook'#comment for Google collab

ERROR: Could not find a version that satisfies the requirement scipy==1.8.1 (from versions: none)
ERROR: No matching distribution found for scipy==1.8.1

[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [5]:
def pyvis_deepnote_show(nt):
    tmp_output_filename = tempfile.NamedTemporaryFile(suffix='.html').name
    nt.save_graph(tmp_output_filename)

    f = open(tmp_output_filename, "r")
    display(HTML(f.read()))

In [42]:
df = pd.read_csv('./FinFraud_unknown.csv', sep=',', parse_dates=[15, 16, 21])

df.columns = [
    'User ID (sender)', 
    'User ID (receiver)',
    'User account ID (sender)',
    'User account ID (receiver)',
    'Amount of transaction',
    'Type of transaction',
    'State of operation',
    'Balance before (sender)',
    'Balance after (sender)',
    'Balance after (receiver)',
    'Balance before (receiver)',    
    'Not used',
    'Not used',
    'Not used',
    'Not used',
    'Transaction timestamp (sender)',
    'Transaction timestamp (receiver)',
    'Sender account ID',
    'Not used',
    'Not used',
    'Not used',
    'Transaction timestamp',
    'Sender type',
    'Receiver type'
]
df = df.loc[:, ~df.columns.str.contains('^Not used', case=False)].sort_values('Transaction timestamp') 
df = df.drop('State of operation', axis=1)
df = df.drop('Sender account ID', axis=1)
df = df.drop('Transaction timestamp (sender)', axis=1)
df = df.drop('Transaction timestamp (receiver)', axis=1)
df = df.drop('Balance before (sender)', axis=1)
df = df.drop('Balance after (sender)', axis=1)
df = df.drop('Balance before (receiver)', axis=1)
df = df.drop('Balance after (receiver)', axis=1)

df["Amount of transaction"] = pd.to_numeric(df["Amount of transaction"], errors='coerce').fillna(0)


df.describe(include='all').fillna('')

User ID (sender) User ID (receiver) User account ID (sender)   
count             54030              54030                    54030  \
unique             1861               1562                     1861   
top             PN_Ret4           operator                    RAcc4   
freq               2256              27901                     2256   
mean                                                                  
std                                                                   
min                                                                   
25%                                                                   
50%                                                                   
75%                                                                   
max                                                                   

       User account ID (receiver) Amount of transaction Type of transaction   
count                       54030               54030.0               54030  \
unique                       1562                                         5   
top                            A0                                      ArRC   
freq                        27901                                     27901   
mean                                        53083.47221                       
std                                         85834.97052                       
min                                                 0.0                       
25%                                           2158.2525                       
50%                                            6257.375                       
75%                                          76821.9675                       
max                                          1053512.86                       

       Transaction timestamp Sender type Receiver type  
count                  54030       54030         54030  
unique                 46394           2             4  
top         08.07.2011 15:16          EU      operator  
freq                       5       41246         27901  
mean                                                    
std                                                     
min                                                     
25%                                                     
50%                                                     
75%                                                     
max

## Описание набора данных


| Название столбца                            | Возможные значения                                                                                                                     |Описание                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              |
|----------------------------------------|----------------------------------------------------------------------------------------------------------------------------|------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| User ID (transaction sender)           | Generated ID                                                                                                               |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| User ID (transaction receiver)         | Generated ID                                                                                                               |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| User account ID (transaction sender)   | Generated ID                                                                                                               |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| User account ID (transaction receiver) | Generated ID                                                                                                               |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Amount of transaction                  | Number                                                                                                                     |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Type of transaction                    | `Ind`<br/>`Dt`<br/>`ArRC`<br/>`Wl`<br/>`Merchant`                                                                          | Тип транзакции <br/>`Ind` – денежный перевод между пользователями системы <br/>`Dt` – пополнение электронного кошелька (отправитель агент, а получатель - пользователь системы)<br/>`ArRC` – пополнение счета мобильной связи (перевод от пользователя системы к оператору мобильной связи )<br/>`Wl` – снятие электронных денег  (отправитель - пользователь системы, получатель - оператор)<br/>`Merchant` – перевод от пользователя поставщику услуг или товаров   |
| State of operation                     | `SU`                                                                                                                       | `SU` – успешно                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Balance before (transaction sender)    | Number                                                                                                                     |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Balance before (transaction receiver)  | Number                                                                                                                     |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Balance after (transaction sender)     | Number                                                                                                                     |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Balance after (transaction receiver)   | Number                                                                                                                     |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Transaction timestamp (sender)         | Datetime                                                                                                                   |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Transaction timestamp (receiver)       | Datetime                                                                                                                   |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Sender account ID                      | Generated ID                                                                                                               |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Transaction timestamp                  | Datetime                                                                                                                   |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Sender type                            | `EU`<br/>`RET`                                                                                                             |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |
| Receiver type                          | `EU`<br/>`operator`<br/>`RET`<br/>`MER`                                                                                    |                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          |


Поскольку поле  `State of operation` всегда имеет значение  (`SU`) для всех транзакций, данный столбец предлагается удалить. 
Столбцы  `Sender account ID` и `User ID (transaction sender)` идентичны, также столбцы `Transaction timestamp (sender)` и `Transaction timestamp (receiver)` идентичны стобцу `Transaction timestamp`, поэтому данные стобцы удалются (остается только `Transaction timestamp`). Также удаляюся столбцы с балансом, т.к. в текущей версии набора данных они не задействованы.

In [43]:
df.dtypes

User ID (sender)               object
User ID (receiver)             object
User account ID (sender)       object
User account ID (receiver)     object
Amount of transaction         float64
Type of transaction            object
Transaction timestamp          object
Sender type                    object
Receiver type                  object
dtype: object

# Статистика транзакций для каждого пользователя

Традиционно начнем со статистического анализа данных. Рекомендуется расширить число рассчитываемых статистик, например, включив показатели, характеризующие частоту транзакций. Для такого вида мошенничества как кража телефона изменение частоты снятий является характерным признаком.

In [44]:
def init_stat_dict():
    stat_dict = dict()
    transaction_types = {"Ind", "Wl", "Dt", "Merchant", "ArRC"} 
    for tran_type in transaction_types:
          amount_name = f"Sent_amount_{tran_type}"
          amount_median = f"Sent_amount_{tran_type}_median"
          amount_min = f"Sent_amount_{tran_type}_min"
          amount_max = f"Sent_amount_{tran_type}_max"
          tran_count = f"Sent_{tran_type}_count"
          rec_amount_name = f"Received_amount_{tran_type}"
          rec_amount_median = f"Received_amount_{tran_type}_median"
          rec_amount_min = f"Received_amount_{tran_type}_min"
          rec_amount_max = f"Received_amount_{tran_type}_max"
          rec_tran_count = f"Received_{tran_type}_count"
          
          stat_dict[amount_name] = 0
          stat_dict[amount_median] = 0
          stat_dict[amount_min] = 0
          stat_dict[amount_max] = 0
          stat_dict[tran_count] = 0
          stat_dict[rec_amount_name] = 0
          stat_dict[rec_amount_median] = 0
          stat_dict[rec_amount_min] = 0
          stat_dict[rec_amount_max] = 0
          stat_dict[rec_tran_count] = 0

    return stat_dict


def get_stat_df(df):
   sent_unique_users = df["User ID (sender)"].unique()
   received_unique_users = df["User ID (receiver)"].unique()
   unique_users = np.unique(np.concatenate((sent_unique_users,received_unique_users),0))
   print(unique_users)
   stat_df = pd.DataFrame()
   stat_dict = init_stat_dict()
   transaction_types = {"Ind", "Wl", "Dt", "Merchant", "ArRC"}
   for user in unique_users:
       stat_dict = init_stat_dict() 
       stat_dict["User ID"] = user

       user_df = df.loc[(df["User ID (sender)"] == user)]
       
       if (not user_df.empty):
          #stat_dict["User ID"] = user
          
          stat_dict["Unique_receivers"] = len(user_df["User ID (receiver)"].unique())
          stat_dict["User type"] = user_df["Sender type"].unique()[0]

          for tran_type in transaction_types:
              amount_name = f"Sent_amount_{tran_type}"
              amount_median = f"Sent_amount_{tran_type}_median"
              amount_min = f"Sent_amount_{tran_type}_min"
              amount_max = f"Sent_amount_{tran_type}_max"
              tran_count = f"Sent_{tran_type}_count"
              stat_dict[amount_name] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].sum()
              stat_dict[amount_median] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].mean()
              stat_dict[amount_min] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].min()
              stat_dict[amount_max] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].max()
              stat_dict[tran_count] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].count()
       else:
          stat_dict["User type"] = (df.loc[(df["User ID (receiver)"]==user)])["Receiver type"].unique()[0]

       user_df = df.loc[(df["User ID (receiver)"] == user)]
       if (not user_df.empty):
          stat_dict["Unique_senders"] = len(user_df["User ID (sender)"].unique())
          for tran_type in transaction_types:
              rec_amount_name = f"Received_amount_{tran_type}"
              rec_amount_median = f"Received_amount_{tran_type}_median"
              rec_amount_min = f"Received_amount_{tran_type}_min"
              rec_amount_max = f"Received_amount_{tran_type}_max"
              rec_tran_count = f"Received_{tran_type}_count"
              stat_dict[rec_amount_name] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].sum()
              stat_dict[rec_amount_median] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].median()
              stat_dict[rec_amount_min] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].min()
              stat_dict[rec_amount_max] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].max()
              stat_dict[rec_tran_count] = (user_df.loc[user_df["Type of transaction"]==tran_type])["Amount of transaction"].count()
       
       df_temp = pd.DataFrame([stat_dict])
       
       #df_temp.head()
       stat_df = pd.concat([stat_df, df_temp])
   stat_df = stat_df.fillna(0)
   return stat_df



Кстати, обратите внимание уникальных пользователей в системе 2009. Это больше, чем число уникальных отправителей и уникальных получателей, значит, какие то пользователи только отправляют деньги, а какие-то только получают.

In [46]:
stat_df = get_stat_df(df)
print(stat_df.shape)
# print(stat_df.head())



['PN_EU_0_0' 'PN_EU_0_1' 'PN_EU_0_10' ... 'PN_Ret5' 'PN_Ret6' 'operator']
(2009, 54)
   Sent_amount_Wl  Sent_amount_Wl_median  Sent_amount_Wl_min   
0             0.0                    0.0                 0.0  \
0             0.0                    0.0                 0.0   
0             0.0                    0.0                 0.0   
0             0.0                    0.0                 0.0   
0             0.0                    0.0                 0.0   

   Sent_amount_Wl_max  Sent_Wl_count  Received_amount_Wl   
0                 0.0              0                 0.0  \
0                 0.0              0                 0.0   
0                 0.0              0                 0.0   
0                 0.0              0                 0.0   
0                 0.0              0                 0.0   

   Received_amount_Wl_median  Received_amount_Wl_min  Received_amount_Wl_max   
0                        0.0                     0.0                     0.0  \
0        

Была выбрана часть статистик и построила проекции пользователей. Анализируемые поля были выбраны на основе анализа свойств возможных финансовых аномалий (т.е. просто эвристически:)).

In [47]:
from pandas.plotting import scatter_matrix
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from matplotlib.ticker import FormatStrFormatter
import plotly.express as px

ModuleNotFoundError: No module named 'sklearn'

# Мошенничество, связанное с заражением бот-сетью.



Согласно описанию сценария атаки: есть множество зараженных пользователей, которые переводят деньги какому-то пользователю ("ослу" или "мулу"), и уже он выполняет операции обналичивания денег. Рассмотрен простейщий вариант сценария: цепочка мулов состоит из одного звена.  

In [48]:

#оставляем поля, связанные с переводами и снятиями и добавили число уникальных пользователей, это же бот сеть.

MobileBot_labels = ['Unique_receivers','Unique_receivers','Sent_Ind_count' ,'Sent_Wl_count', 'Received_Ind_count']

# а по этим полям будем пробовать найти пользователей с кражей телефона.
MobileTheft_labels = ['Sent_amount_Wl', 'Sent_amount_Wl_median', 'Sent_amount_Wl_min', 'Sent_amount_Wl_max', 'Sent_Wl_count']

x = stat_df[MobileBot_labels].values

# нормализуем значения
x = StandardScaler().fit_transform(x)

pca = PCA(n_components=3)
principalComponents = pca.fit_transform(x)
print(f'Explained variance: {pca.explained_variance_ratio_}\tSum: {pca.explained_variance_ratio_.sum()}')


NameError: name 'StandardScaler' is not defined